# High-performance RAG (and Evaluation) with LlamaIndex

#### fine-tuning embeddings model
#### expanding context window from retieved node

In [1]:
import nest_asyncio

nest_asyncio.apply()

In [2]:
import os
import dotenv

dotenv.load_dotenv()

True

# loading the data

In [3]:
#!git clone https://github.com/AI-Maker-Space/DataRepository.git

In [4]:
%cd DataRepository/high-performance-rag 

d:\pythonProjects\LammaIndex\advanceRAG\DataRepository\high-performance-rag


In [5]:
# build the dataset 

In [6]:
from llama_index.core.node_parser import SimpleNodeParser
from llama_index.core.schema import MetadataMode

TRAIN_FILES="data/CamelPapersTrain"
TEST_FILES="data/CamelPapersTest"

In [7]:
from llama_index.core import SimpleDirectoryReader

def load_corpus(directory,verbose=False):
    if verbose:
        print(f'Loading files in {directory}')
    reader=SimpleDirectoryReader(directory)
    docs=reader.load_data()
    if verbose:
        print(f'loaded {len(docs)} docs')
    parser=SimpleNodeParser.from_defaults()
    nodes=parser.get_nodes_from_documents(docs,show_progress=verbose)
    if verbose:
        print(f'Paesed {len(nodes)} nodes')
    return nodes 


In [8]:
%cd /pythonProjects/LammaIndex/advanceRAG/
train_nodes=load_corpus(TRAIN_FILES,verbose=True)
val_nodes=load_corpus(TEST_FILES,verbose=True)

d:\pythonProjects\LammaIndex\advanceRAG
Loading files in data/CamelPapersTrain
loaded 91 docs


d:\anaconda\envs\pytorch\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Parsing nodes: 100%|██████████| 91/91 [00:00<00:00, 349.90it/s]


Paesed 156 nodes
Loading files in data/CamelPapersTest
loaded 9 docs


Parsing nodes: 100%|██████████| 9/9 [00:00<00:00, 230.30it/s]

Paesed 17 nodes


# constructing fine-tuned database

In [9]:
from llama_index.finetuning import generate_qa_embedding_pairs, EmbeddingQAFinetuneDataset

In [10]:
from llama_index.llms.azure_openai import AzureOpenAI
from llama_index.embeddings.azure_openai import AzureOpenAIEmbedding

llm=AzureOpenAI(
    model='gpt-4',
    deployment_name='gpt-4',
    api_key=os.getenv('AZURE_OPENAI_API_KEY'),
    azure_endpoint=os.getenv('AZURE_OPENAI_ENDPOINT'),
    api_version='2024-02-15-preview'
)
embed_model = AzureOpenAIEmbedding(
    model="text-embedding-ada-002",
    deployment_name="text-embedding-ada-002",
    api_key=os.getenv('AZURE_OPENAI_API_KEY'),
    azure_endpoint=os.getenv('AZURE_EMBEDDING_ENDPOINT'),
    api_version='2024-02-15-preview'
)


In [11]:
# train_dataset=generate_qa_embedding_pairs(train_nodes,llm=llm)
# train_dataset.save_json('train_dataset.json')

In [12]:
# train_dataset.save_json("train_dataset.json")

In [13]:
train_dataset=EmbeddingQAFinetuneDataset.from_json('train_dataset.json')


In [14]:
# val_dataset=generate_qa_embedding_pairs(val_nodes,llm=llm)
# val_dataset.save_json('val_dataset.json')

In [15]:
val_dataset=EmbeddingQAFinetuneDataset.from_json('val_dataset.json')

In [16]:
import torch
torch.cuda.is_available()

True

# Fine-Tuning BAAI/bge-small-en-v1.5

In [17]:
from llama_index.finetuning import SentenceTransformersFinetuneEngine

finetune_engine=SentenceTransformersFinetuneEngine(
    train_dataset,
    model_id='BAAI/bge-small-en-v1.5',
    model_output_path='llama_model_v1',
    val_dataset=val_dataset,
    epochs=2,
    device='cuda'
    
)

INFO:datasets:PyTorch version 2.5.1 available.
PyTorch version 2.5.1 available.
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: BAAI/bge-small-en-v1.5
Load pretrained SentenceTransformer: BAAI/bge-small-en-v1.5


In [18]:
finetune_engine.finetune()

 50%|█████     | 32/64 [00:09<00:07,  4.36it/s]

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Information Retrieval Evaluation of the model on the  dataset after epoch 1.0:
Information Retrieval Evaluation of the model on the  dataset after epoch 1.0:
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Queries: 312
Queries: 312
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Corpus: 156

Corpus: 156

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Score-Function: cosine
Score-Function: cosine
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@1: 59.29%
Accuracy@1: 59.29%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@3: 81.41%
Accuracy@3: 81.41%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@5: 89.10%
Accuracy@5: 89.10%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@10: 95.19%
Accuracy@10: 95.19%
INFO:sentence_transformers.evaluation.Informat

 78%|███████▊  | 50/64 [00:16<00:03,  3.58it/s]

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Information Retrieval Evaluation of the model on the  dataset:
Information Retrieval Evaluation of the model on the  dataset:
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Queries: 312
Queries: 312
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Corpus: 156

Corpus: 156

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Score-Function: cosine
Score-Function: cosine
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@1: 62.18%
Accuracy@1: 62.18%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@3: 82.69%
Accuracy@3: 82.69%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@5: 89.74%
Accuracy@5: 89.74%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@10: 96.15%
Accuracy@10: 96.15%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Precision@

 78%|███████▊  | 50/64 [00:17<00:03,  3.58it/s]

{'eval_cosine_accuracy@1': 0.6217948717948718, 'eval_cosine_accuracy@3': 0.8269230769230769, 'eval_cosine_accuracy@5': 0.8974358974358975, 'eval_cosine_accuracy@10': 0.9615384615384616, 'eval_cosine_precision@1': 0.6217948717948718, 'eval_cosine_precision@3': 0.27564102564102566, 'eval_cosine_precision@5': 0.17948717948717946, 'eval_cosine_precision@10': 0.09615384615384615, 'eval_cosine_recall@1': 0.6217948717948718, 'eval_cosine_recall@3': 0.8269230769230769, 'eval_cosine_recall@5': 0.8974358974358975, 'eval_cosine_recall@10': 0.9615384615384616, 'eval_cosine_ndcg@10': 0.7911491260645935, 'eval_cosine_mrr@10': 0.7363871082621082, 'eval_cosine_map@100': 0.7391352027768923, 'eval_dot_accuracy@1': 0.6217948717948718, 'eval_dot_accuracy@3': 0.8269230769230769, 'eval_dot_accuracy@5': 0.8974358974358975, 'eval_dot_accuracy@10': 0.9615384615384616, 'eval_dot_precision@1': 0.6217948717948718, 'eval_dot_precision@3': 0.27564102564102566, 'eval_dot_precision@5': 0.17948717948717946, 'eval_dot_

 98%|█████████▊| 63/64 [00:21<00:00,  3.70it/s]

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Information Retrieval Evaluation of the model on the  dataset after epoch 2.0:
Information Retrieval Evaluation of the model on the  dataset after epoch 2.0:
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Queries: 312
Queries: 312
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Corpus: 156

Corpus: 156

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Score-Function: cosine
Score-Function: cosine
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@1: 62.18%
Accuracy@1: 62.18%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@3: 82.37%
Accuracy@3: 82.37%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@5: 89.74%
Accuracy@5: 89.74%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@10: 96.47%
Accuracy@10: 96.47%
INFO:sentence_transformers.evaluation.Informat

100%|██████████| 64/64 [00:23<00:00,  2.71it/s]

{'train_runtime': 23.6528, 'train_samples_per_second': 26.382, 'train_steps_per_second': 2.706, 'train_loss': 0.4020216464996338, 'epoch': 2.0}


In [19]:
import torch
torch.cuda.is_available()

True

In [21]:
finetuned_embedding_model=finetune_engine.get_finetuned_model()
finetuned_embedding_model.to_json()

INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: llama_model_v1
Load pretrained SentenceTransformer: llama_model_v1


INFO:sentence_transformers.SentenceTransformer:2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']


'{"model_name": "llama_model_v1", "embed_batch_size": 10, "num_workers": null, "max_length": 512, "normalize": true, "query_instruction": null, "text_instruction": null, "cache_folder": null, "class_name": "HuggingFaceEmbedding"}'

In [24]:
from llama_index.embeddings.huggingface import HuggingFaceEmbedding

embed_model=HuggingFaceEmbedding(model_name='llama_model_v1')

INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: llama_model_v1
Load pretrained SentenceTransformer: llama_model_v1
INFO:sentence_transformers.SentenceTransformer:2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']


In [ ]:
# !zip -r /content/file.zip llama_model_v1

'zip' is not recognized as an internal or external command,
operable program or batch file.


# Evaluating Embeddings model

In [29]:
from sentence_transformers.evaluation import InformationRetrievalEvaluator
from sentence_transformers import SentenceTransformer
from pathlib import Path

In [30]:
def evaluate_st(
        dataset,
        model_id,
        name,
):
    corpus=dataset.corpus
    queries=dataset.queries
    relevant_docs=dataset.relevant_docs

    evaluator=InformationRetrievalEvaluator(queries,corpus,relevant_docs,name=name)
    model=SentenceTransformer(model_id)
    output_path='results/'
    Path(output_path).mkdir(exist_ok=True,parents=True)
    return evaluator(model,output_path=output_path)

In [31]:
evaluate_st(val_dataset,'BAAI/bge-small-en-v1.5',name='bge')

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: cuda
Use pytorch device_name: cuda
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: BAAI/bge-small-en-v1.5
Load pretrained SentenceTransformer: BAAI/bge-small-en-v1.5
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Information Retrieval Evaluation of the model on the bge dataset:
Information Retrieval Evaluation of the model on the bge dataset:
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Queries: 312
Queries: 312
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Corpus: 156

Corpus: 156

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Score-Function: cosine
Score-Function: cosine
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@1: 49.68%
Accuracy@1: 49.68%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@3: 71.47%
Accuracy@3: 71.47%
INFO:sentenc

{'bge_cosine_accuracy@1': 0.4967948717948718,
 'bge_cosine_accuracy@3': 0.7147435897435898,
 'bge_cosine_accuracy@5': 0.8012820512820513,
 'bge_cosine_accuracy@10': 0.8878205128205128,
 'bge_cosine_precision@1': 0.4967948717948718,
 'bge_cosine_precision@3': 0.2382478632478633,
 'bge_cosine_precision@5': 0.16025641025641027,
 'bge_cosine_precision@10': 0.08878205128205127,
 'bge_cosine_recall@1': 0.4967948717948718,
 'bge_cosine_recall@3': 0.7147435897435898,
 'bge_cosine_recall@5': 0.8012820512820513,
 'bge_cosine_recall@10': 0.8878205128205128,
 'bge_cosine_ndcg@10': 0.69066361056788,
 'bge_cosine_mrr@10': 0.6274572649572648,
 'bge_cosine_map@100': 0.6328873016285366,
 'bge_dot_accuracy@1': 0.4967948717948718,
 'bge_dot_accuracy@3': 0.7147435897435898,
 'bge_dot_accuracy@5': 0.8012820512820513,
 'bge_dot_accuracy@10': 0.8878205128205128,
 'bge_dot_precision@1': 0.4967948717948718,
 'bge_dot_precision@3': 0.2382478632478633,
 'bge_dot_precision@5': 0.16025641025641027,
 'bge_dot_preci

In [32]:
evaluate_st(val_dataset, "llama_model_v1", name="finetuned")

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: cuda
Use pytorch device_name: cuda
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: llama_model_v1
Load pretrained SentenceTransformer: llama_model_v1
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Information Retrieval Evaluation of the model on the finetuned dataset:
Information Retrieval Evaluation of the model on the finetuned dataset:
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Queries: 312
Queries: 312
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Corpus: 156

Corpus: 156

INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Score-Function: cosine
Score-Function: cosine
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@1: 62.18%
Accuracy@1: 62.18%
INFO:sentence_transformers.evaluation.InformationRetrievalEvaluator:Accuracy@3: 82.37%
Accuracy@3: 82.37%
INFO:sentence_tr

{'finetuned_cosine_accuracy@1': 0.6217948717948718,
 'finetuned_cosine_accuracy@3': 0.8237179487179487,
 'finetuned_cosine_accuracy@5': 0.8974358974358975,
 'finetuned_cosine_accuracy@10': 0.9647435897435898,
 'finetuned_cosine_precision@1': 0.6217948717948718,
 'finetuned_cosine_precision@3': 0.27457264957264954,
 'finetuned_cosine_precision@5': 0.17948717948717946,
 'finetuned_cosine_precision@10': 0.09647435897435896,
 'finetuned_cosine_recall@1': 0.6217948717948718,
 'finetuned_cosine_recall@3': 0.8237179487179487,
 'finetuned_cosine_recall@5': 0.8974358974358975,
 'finetuned_cosine_recall@10': 0.9647435897435898,
 'finetuned_cosine_ndcg@10': 0.7923766083582862,
 'finetuned_cosine_mrr@10': 0.7370764652014652,
 'finetuned_cosine_map@100': 0.7396023091936553,
 'finetuned_dot_accuracy@1': 0.6217948717948718,
 'finetuned_dot_accuracy@3': 0.8237179487179487,
 'finetuned_dot_accuracy@5': 0.8974358974358975,
 'finetuned_dot_accuracy@10': 0.9647435897435898,
 'finetuned_dot_precision@1': 0

# advanced retrieval method: sentence window retrieval
- We parse our document into sentence-wise nodes.
- We find the most relevant sentence-wise nodes to our query.
- We add additional context based on a "window" around that base sentence-wise node.
- We use that enhanced context as context for our LLM!

In [36]:
#example of how we are splitting the data
block_1 = """
I went to Tosche Station. I bought a Power Converter. I live on a planet with 2 Moons. My name is Luke Skywalker.
"""

sentences=block_1.split(".")
print(sentences)

chunks=[block_1[:50],block_1[50:100],block_1[100:]]
print(chunks)

['\nI went to Tosche Station', ' I bought a Power Converter', ' I live on a planet with 2 Moons', ' My name is Luke Skywalker', '\n']
['\nI went to Tosche Station. I bought a Power Conver', 'ter. I live on a planet with 2 Moons. My name is L', 'uke Skywalker.\n']


In [74]:
# from llama_index.core import ServiceContext,set_global_service_context
from llama_index.core.settings import Settings
from llama_index.llms.azure_openai import AzureOpenAI
from llama_index.embeddings.azure_openai import AzureOpenAIEmbedding
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core.node_parser import SentenceWindowNodeParser, SimpleNodeParser

settings_base=Settings
settings_tuned=Settings
#window node parser
settings_tuned.node_parser=SentenceWindowNodeParser.from_defaults(
    window_size=6,
    window_metadata_key='window',
    original_text_metadata_key='original_text'
)

#simple node parser
settings_base.simple_node_parser=SimpleNodeParser.from_defaults()
# settings_tuned.simple_node_parser=SimpleNodeParser.from_defaults()
#base query Engine LLM
settings_base.llm=AzureOpenAI(
    model='gpt-4',
    deployment_name='gpt-4',
    api_key=os.getenv('AZURE_OPENAI_API_KEY'),
    azure_endpoint=os.getenv('AZURE_OPENAI_ENDPOINT'),
    api_version='2024-02-15-preview'
)
settings_tuned.llm=AzureOpenAI(
    model='gpt-4',
    deployment_name='gpt-4',
    api_key=os.getenv('AZURE_OPENAI_API_KEY'),
    azure_endpoint=os.getenv('AZURE_OPENAI_ENDPOINT'),
    api_version='2024-02-15-preview'
)
#base embedding model
settings_base.embed_model_base=HuggingFaceEmbedding(
    model_name='BAAI/bge-small-en'
)

#fine-tuned embeddings model
settings_tuned.embed_model=HuggingFaceEmbedding(
    model_name='llama_model_v1'
)

# #fine-tuned Service Context
# ctx=ServiceContext.from_defaults(
#     llm=llm,
#     embed_model=embed_model
# )

# #base Service Context
# ctx_base=ServiceContext.from_defaults(
#     llm=llm,
#     embed_model=embed_model
# )


INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: BAAI/bge-small-en
Load pretrained SentenceTransformer: BAAI/bge-small-en


INFO:sentence_transformers.SentenceTransformer:2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: llama_model_v1
Load pretrained SentenceTransformer: llama_model_v1
INFO:sentence_transformers.SentenceTransformer:2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']


In [47]:
documents=SimpleDirectoryReader(
    TRAIN_FILES
).load_data()

In [ ]:
nodes=settings_tuned.node_parser.get_nodes_from_documents(documents)
base_nodes=settings_base.simple_node_parser.get_nodes_from_documents(documents)


[TextNode(id_='c27b6976-f32d-4a57-85c7-85b0e54039e5', embedding=None, metadata={'page_label': '1', 'file_name': 'Antibody response to the epsilon toxin ofClostridium perfringensfollowing vaccination of Lama glamacrias.pdf', 'file_path': 'd:\\pythonProjects\\LammaIndex\\advanceRAG\\data\\CamelPapersTrain\\Antibody response to the epsilon toxin ofClostridium perfringensfollowing vaccination of Lama glamacrias.pdf', 'file_type': 'application/pdf', 'file_size': 137191, 'creation_date': '2023-10-09', 'last_modified_date': '2023-10-09', 'window': '   Brief Original Article  \n \nAntibody response to the epsilon toxin of  Clostridium perfringens  following \nvaccination of Lama glama  crias  \n \nAdriana B. Bentancor1, Pablo Halperi n2 Myriam Flores3, Fabián Iribarren4,5 \n \n1Microbiología,  2Histología, 3Estadística, 4Enfermedades Infecciosas , Facultad de Ciencias Veterinarias  Universidad de Buenos \nAires, Argentina,  Chorroarín 280.   Cdad.  Autónoma de Buenos Aires,  Argentina   \n5Ins

# create vectorStoreIndex for each set of nodes

In [87]:
from llama_index.core import VectorStoreIndex
sentence_index=VectorStoreIndex(nodes,settings_tuned)

Batches: 100%|██████████| 1/1 [00:00<00:00, 18.77it/s]


In [88]:
sentence_index.storage_context.persist(persist_dir='sentence_index')

In [89]:
base_index=VectorStoreIndex(base_nodes,settings_base)
base_index.storage_context.persist(persist_dir='base_index')

Batches: 100%|██████████| 1/1 [00:00<00:00, 43.88it/s]


- MetadataReplacementPostProcessor - replace sebtebces (original_text) with expanded contexts (window)
- top_k - retrieving the top 3 sentences 
- converting them to their surrounding context 

In [90]:
from llama_index.core.indices.postprocessor import MetadataReplacementPostProcessor

query_engine=sentence_index.as_query_engine(
    similarity_top_k=3,
    node_postprocessors=[MetadataReplacementPostProcessor(target_metadata_key="window")],
)

In [91]:
window_response=query_engine.query('How do camelig genetics influence wool quality?')

Batches: 100%|██████████| 1/1 [00:00<00:00,  8.81it/s]


INFO:httpx:HTTP Request: POST https://easttest123.openai.azure.com//openai/deployments/gpt-4/chat/completions?api-version=2024-02-15-preview "HTTP/1.1 200 OK"
HTTP Request: POST https://easttest123.openai.azure.com//openai/deployments/gpt-4/chat/completions?api-version=2024-02-15-preview "HTTP/1.1 200 OK"


In [92]:
window_response.source_nodes

[NodeWithScore(node=TextNode(id_='e32c6544-c8cd-4543-92c2-35e149109fa5', embedding=None, metadata={'page_label': '79', 'file_name': 'Influence of effects on quality traits and relationships between traits of the llama fleece..pdf', 'file_path': 'd:\\pythonProjects\\LammaIndex\\advanceRAG\\data\\CamelPapersTrain\\Influence of effects on quality traits and relationships between traits of the llama fleece..pdf', 'file_type': 'application/pdf', 'file_size': 40813065, 'creation_date': '2023-10-09', 'last_modified_date': '2023-10-09', 'window': '79 August 2022, Vol.  12, No.  4\nbe studied.  The purpose of this review is to update the reader \non the current state of knowledge of fiber genetics in domestic South American camelids and to discuss how genomics and the emergence of modern technologies for sequencing and discovering genetic variants will contribute to the advancement in this field.\n Coat Color Genetics\nLlamas and alpacas have more than 22 natural colors ran -\nging from black a

In [93]:
# check original sentence and their expanded context window

window=window_response.source_nodes[0].node.metadata['window']
sentence=window_response.source_nodes[0].node.metadata['original_text']

print(f'Window: {window}')
print(f'Original Sentence: {sentence}')

Window: 79 August 2022, Vol.  12, No.  4
be studied.  The purpose of this review is to update the reader 
on the current state of knowledge of fiber genetics in domestic South American camelids and to discuss how genomics and the emergence of modern technologies for sequencing and discovering genetic variants will contribute to the advancement in this field.
 Coat Color Genetics
Llamas and alpacas have more than 22 natural colors ran -
ging from black and brown through gray and fawn to white, including all intermediate shades.  Llamas present greater color variation compared to alpacas; tricolor phenotypes may be ob -
served and the presence of white spots is common in llamas.  Additionally, this variety of colors and patterns normally oc -
curs in the same herd, unlike alpaca’s herds that tend to be more homogeneous.  The difference can be attributed to the se -
lection process during the domestication of each species.  The 
llama, as a multipurpose animal, was selected for greater bo

- compute the same with simple nodes

In [95]:
query_engine=base_index.as_query_engine(similarity_top_k=2)
vector_response=query_engine.query("How do camelid genetics influence wool quality?")

Batches: 100%|██████████| 1/1 [00:00<00:00, 10.42it/s]


INFO:httpx:HTTP Request: POST https://easttest123.openai.azure.com//openai/deployments/gpt-4/chat/completions?api-version=2024-02-15-preview "HTTP/1.1 200 OK"
HTTP Request: POST https://easttest123.openai.azure.com//openai/deployments/gpt-4/chat/completions?api-version=2024-02-15-preview "HTTP/1.1 200 OK"


In [96]:
vector_response.response

'Camelid genetics play a significant role in determining the quality of wool through the control of various fiber traits. These traits can be broadly categorized into qualitative and quantitative types. Qualitative traits, such as fleece color and type, are controlled by one or several genes and are less influenced by environmental factors. On the other hand, quantitative traits, like the amount of fiber produced and the fineness of the fiber, are influenced by multiple genes and are also affected by environmental conditions. Understanding the genetic mechanisms that regulate these traits can assist breeders in selecting and improving the productive characteristics of camelids, ultimately enhancing wool quality. Additionally, advancements in genetic research, such as the development of SNP arrays, facilitate the identification of genes associated with complex traits, further aiding in the genetic improvement of camelid wool.'

# Evaluating our pipeline
- datasetGenerator - query responseDataset using gpt-4
- usually we do evaluation with the latest good model 

In [ ]:
import random
from llama_index.core.evaluation import DatasetGenerator,QueryResponseDataset

# no of nodes to evaluate 
num_nodes_eval=10

# selecting a ranondom sample of nodes 